In [1]:
#!conda install -c conda-forge geopy --yes

In [2]:
#!conda install -c conda-forge folium=0.5.0 --yes

In [3]:
import numpy as np 
import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json 
from geopy.geocoders import Nominatim
import requests 
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium

In [4]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset

In [5]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [6]:
neighborhoods_data = newyork_data['features']

In [7]:
column_names = ['Neighborhood', 'Latitude', 'Longitude']

In [8]:
df = pd.DataFrame(columns=column_names)

In [9]:
for data in neighborhoods_data:
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    df = df.append({
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [10]:
df.head()

Neighborhood   Latitude  Longitude
0    Wakefield  40.894705 -73.847201
1   Co-op City  40.874294 -73.829939
2  Eastchester  40.887556 -73.827806
3    Fieldston  40.895437 -73.905643
4    Riverdale  40.890834 -73.912585

In [11]:
df.to_csv("df.csv", index=False)

In [12]:
address = 'New York, US'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

In [13]:
map_ny = folium.Map(location=[latitude, longitude], zoom_start=11)
for lat, lng, neighborhood in zip(df['Latitude'], df['Longitude'], df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_ny)  
    
map_ny

In [14]:
map_ny.save('map_ny.html')

In [15]:
CLIENT_ID = 'YOWIPYAE1F1PQMGEXZTMD1BXUDJPAKUI55FY412I25GIRGNJ' 
CLIENT_SECRET = '4LEJRXJXEDMD3XT2VWZIESHXZCF1JSWM3AMFVT3O4RFRQR02' 
VERSION = '20180605' 

In [16]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(df['Latitude'], df['Longitude'], df['Neighborhood']):
    
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [17]:
venues_df = pd.DataFrame(venues)

In [18]:
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

In [19]:
venues_df.head()

Neighborhood   Latitude  Longitude                 VenueName  VenueLatitude  \
0    Wakefield  40.894705 -73.847201          Lollipops Gelato      40.894123   
1    Wakefield  40.894705 -73.847201        Ripe Kitchen & Bar      40.898152   
2    Wakefield  40.894705 -73.847201           Ali's Roti Shop      40.894036   
3    Wakefield  40.894705 -73.847201                   Jimbo's      40.891740   
4    Wakefield  40.894705 -73.847201  Kingston Tropical Bakery      40.888568   

   VenueLongitude         VenueCategory  
0      -73.845892          Dessert Shop  
1      -73.838875  Caribbean Restaurant  
2      -73.856935  Caribbean Restaurant  
3      -73.858226          Burger Joint  
4      -73.859885                Bakery

In [20]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                               
Allerton                        100        100        100            100   
Annadale                         60         60         60             60   
Arden Heights                    93         93         93             93   
Arlington                        53         53         53             53   
Arrochar                         78         78         78             78   
Arverne                          56         56         56             56   
Astoria                         100        100        100            100   
Astoria Heights                 100        100        100            100   
Auburndale                      100        100        100            100   
Bath Beach                      100        100        100            100   
Battery Park City               100        100        100            100   
Bay Ridge                       100        100        100            100   
Bay Terrace                     138        138        138            138   
Baychester                      100        100        100            100   
Bayside                         100        100        100            100   
Bayswater                        40         40         40             40   
Bedford Park                    100        100        100            100   
Bedford Stuyvesant              100        100        100            100   
Beechhurst                       95         95         95             95   
Bellaire                        100        100        100            100   
Belle Harbor                     54         54         54             54   
Bellerose                       100        100        100            100   
Belmont                         100        100        100            100   
Bensonhurst                     100        100        100            100   
Bergen Beach                     92         92         92             92   
Blissville                      100        100        100            100   
Bloomfield                       32         32         32             32   
Boerum Hill                     100        100        100            100   
Borough Park                    100        100        100            100   
Breezy Point                     21         21         21             21   
Briarwood                       100        100        100            100   
Brighton Beach                  100        100        100            100   
Broad Channel                    42         42         42             42   
Broadway Junction               100        100        100            100   
Bronxdale                       100        100        100            100   
Brooklyn Heights                100        100        100            100   
Brookville                       47         47         47             47   
Brownsville                     100        100        100            100   
Bulls Head                      100        100        100            100   
Bushwick                        100        100        100            100   
Butler Manor                     47         47         47             47   
Cambria Heights                  72         72         72             72   
Canarsie                        100        100        100            100   
Carnegie Hill                   100        100        100            100   
Carroll Gardens                 100        100        100            100   
Castle Hill                      78         78         78             78   
Castleton Corners               100        100        100            100   
Central Harlem                  100        100        100            100   
Charleston                       82         82         82             82   
Chelsea                         136        136        136            136   
Chinatown                       100        100        100            100   

In [21]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 436 uniques categories.


In [22]:
venues_df['VenueCategory'].unique()[:436]

array(['Dessert Shop', 'Caribbean Restaurant', 'Burger Joint', 'Bakery',
       'Ice Cream Shop', 'Deli / Bodega', 'Pizza Place', 'Pub',
       'Pharmacy', 'Italian Restaurant', 'Seafood Restaurant',
       'Indian Restaurant', 'Breakfast Spot', 'Diner', 'Donut Shop',
       'Historic Site', 'Bagel Shop', 'Fast Food Restaurant',
       'Mobile Phone Shop', 'American Restaurant', 'Spa',
       'Sandwich Place', 'Bar', 'Grocery Store', 'Arcade', 'Restaurant',
       'Nightclub', 'Gas Station', 'Supermarket', 'Bank',
       'Shipping Store', 'Rental Car Location', 'Convenience Store',
       'Shopping Mall', 'Asian Restaurant', 'Cocktail Bar',
       'Discount Store', 'Dumpling Restaurant', 'Spanish Restaurant',
       'Mexican Restaurant', 'Kids Store', 'Gym / Fitness Center',
       'Shoe Store', 'Lingerie Store', 'Clothing Store', 'BBQ Joint',
       'Steakhouse', 'Department Store', 'Coffee Shop', 'Liquor Store',
       'Furniture / Home Store', 'Cosmetics Shop', 'Dance Studio',
     

In [23]:
"Pharmacy" in venues_df['VenueCategory'].unique()

True

In [24]:
ny_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")
ny_onehot['Neighborhoods'] = venues_df['Neighborhood'] 
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]
ny_onehot.head()

Neighborhoods  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Wakefield                  0               0                  0   
1     Wakefield                  0               0                  0   
2     Wakefield                  0               0                  0   
3     Wakefield                  0               0                  0   
4     Wakefield                  0               0                  0   

   African Restaurant  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Animal Shelter  Antique Shop  Aquarium  Arcade  \
0                    0               0             0         0       0   
1                    0               0             0         0       0   
2                    0               0             0         0       0   
3                    0               0             0         0       0   
4                    0               0             0         0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Automotive Shop  BBQ Joint  Bagel Shop  Baggage Locker  \
0            0                0          0           0               0   
1            0                0          0           0               0   
2            0                0          0           0               0   
3            0                0          0           0               0   
4            0                0          0           0               0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       1     0    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                   0           0      0          0                0   
1                   0           0      0          0                0   
2                   0           0      0          0                0   
3                   0           0      0          0                0   
4                   0           0      0          0                0   

   Beer B

In [25]:
ny_grouped = ny_onehot.groupby(["Neighborhoods"]).mean().reset_index()
ny_grouped

Neighborhoods  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000            0.00   
1                     Annadale           0.000000            0.00   
2                Arden Heights           0.000000            0.00   
3                    Arlington           0.000000            0.00   
4                     Arrochar           0.000000            0.00   
5                      Arverne           0.000000            0.00   
6                      Astoria           0.000000            0.00   
7              Astoria Heights           0.000000            0.00   
8                   Auburndale           0.000000            0.00   
9                   Bath Beach           0.000000            0.00   
10           Battery Park City           0.000000            0.00   
11                   Bay Ridge           0.000000            0.00   
12                 Bay Terrace           0.000000            0.00   
13                  Baychester           0.010000            0.00   
14                     Bayside           0.000000            0.00   
15                   Bayswater           0.000000            0.00   
16                Bedford Park           0.000000            0.00   
17          Bedford Stuyvesant           0.000000            0.00   
18                  Beechhurst           0.000000            0.00   
19                    Bellaire           0.000000            0.00   
20                Belle Harbor           0.000000            0.00   
21                   Bellerose           0.000000            0.00   
22                     Belmont           0.000000            0.00   
23                 Bensonhurst           0.000000            0.00   
24                Bergen Beach           0.021739            0.00   
25                  Blissville           0.000000            0.00   
26                  Bloomfield           0.000000            0.00   
27                 Boerum Hill           0.000000            0.00   
28                Borough Park           0.000000            0.00   
29                Breezy Point           0.000000            0.00   
30                   Briarwood           0.000000            0.00   
31              Brighton Beach           0.000000            0.00   
32               Broad Channel           0.000000            0.00   
33           Broadway Junction           0.000000            0.00   
34                   Bronxdale           0.000000            0.00   
35            Brooklyn Heights           0.000000            0.00   
36                  Brookville           0.021277            0.00   
37                 Brownsville           0.000000            0.00   
38                  Bulls Head           0.000000            0.00   
39                    Bushwick           0.000000            0.00   
40                Butler Manor           0.000000            0.00   
41             Cambria Heights           0.000000            0.00   
42                    Canarsie           0.000000            0.00   
43               Carnegie Hill           0.000000            0.00   
44             Carroll Gardens           0.000000            0.00   
45                 Castle Hill           0.000000            0.00   
46           Castleton Corners           0.000000            0.00   
47              Central Harlem           0.000000            0.00   
48                  Charleston           0.000000            0.00   
49                     Chelsea           0.000000            0.00   
50                   Chinatown           0.000000            0.00   
51                 City Island           0.000000            0.00   
52                   City Line           0.000000            0.00   
53                Civic Center           0.000000            0.00   
54           Claremont Village           0.000000            0.00   
55                Clason Point           0.000000            0.00   
56                     Clifton           0.000000            0.00   
57             

In [26]:
len(ny_grouped[ny_grouped["Pharmacy"] > 0])

194

In [27]:
ny_doc = ny_grouped[["Neighborhoods","Pharmacy"]]

In [28]:
ny_doc.head()

Neighborhoods  Pharmacy
0       Allerton  0.030000
1       Annadale  0.050000
2  Arden Heights  0.021505
3      Arlington  0.018868
4       Arrochar  0.025641

In [29]:
kclusters = 3

ny_clustering = ny_doc.drop(["Neighborhoods"], 1)
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_clustering)
kmeans.labels_[0:10]

array([2, 0, 2, 2, 2, 1, 1, 1, 2, 0], dtype=int32)

In [30]:
ny_merged = ny_doc.copy()
ny_merged["Cluster Labels"] = kmeans.labels_

In [31]:
ny_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
ny_merged.head()

Neighborhood  Pharmacy  Cluster Labels
0       Allerton  0.030000               2
1       Annadale  0.050000               0
2  Arden Heights  0.021505               2
3      Arlington  0.018868               2
4       Arrochar  0.025641               2

In [32]:
ny_merged = ny_merged.join(df.set_index("Neighborhood"), on="Neighborhood")
ny_merged.head()

Neighborhood  Pharmacy  Cluster Labels   Latitude  Longitude
0       Allerton  0.030000               2  40.865788 -73.859319
1       Annadale  0.050000               0  40.538114 -74.178549
2  Arden Heights  0.021505               2  40.549286 -74.185887
3      Arlington  0.018868               2  40.635325 -74.165104
4       Arrochar  0.025641               2  40.596313 -74.067124

In [33]:
ny_merged.sort_values(["Cluster Labels"], inplace=True)
ny_merged

Neighborhood  Pharmacy  Cluster Labels   Latitude  Longitude
217               Prince's Bay  0.044444               0  40.526264 -74.201526
178                Mill Island  0.050000               0  40.606336 -73.908186
228             Remsen Village  0.040000               0  40.652117 -73.916653
54           Claremont Village  0.050000               0  40.831428 -73.901199
109                 Georgetown  0.040000               0  40.623845 -73.916075
234                   Rochdale  0.050000               0  40.675211 -73.772588
236              Rockaway Park  0.048387               0  40.580343 -73.841534
166              Manor Heights  0.046154               0  40.601810 -74.120594
244              Schuylerville  0.043011               0  40.826580 -73.826203
46           Castleton Corners  0.040000               0  40.613336 -74.119181
45                 Castle Hill  0.038462               0  40.819014 -73.848027
87                 Egbertville  0.040000               0  40.579119 -74.127272
42                    Canarsie  0.060000               0  40.635564 -73.902093
41             Cambria Heights  0.083333               0  40.692775 -73.735269
40                Butler Manor  0.042553               0  40.506082 -74.229504
251                  Soundview  0.040000               0  40.821012 -73.865746
59                  Co-op City  0.050000               0  40.874294 -73.829939
115               Graniteville  0.040000               0  40.620172 -74.153152
182                 Morrisania  0.040000               0  40.823592 -73.901506
98                   Flatlands  0.040000               0  40.630446 -73.929113
91                Emerson Hill  0.050633               0  40.606794 -74.097762
201              Ocean Parkway  0.050000               0  40.613060 -73.968367
84                    Edenwald  0.060000               0  40.884561 -73.848083
83                 Eastchester  0.070000               0  40.887556 -73.827806
202                   Old Town  0.040000               0  40.596329 -74.087511
203                  Olinville  0.040000               0  40.871371 -73.863324
204                 Ozone Park  0.040000               0  40.680708 -73.843203
205            Paerdegat Basin  0.060000               0  40.631318 -73.902335
77               East Flatbush  0.050000               0  40.641718 -73.936103
210             Pelham Gardens  0.040000               0  40.862966 -73.841612
212            Pleasant Plains  0.039474               0  40.524699 -74.219831
192            New Springville  0.050000               0  40.594252 -74.164960
71                Dongan Hills  0.040000               0  40.588673 -74.096399
138                Hunts Point  0.064103               0  40.809730 -73.883315
67                Country Club  0.040000               0  40.844246 -73.824099
221             Queens Village  0.040000               0  40.718893 -73.738715
36                  Brookville  0.042553               0  40.660003 -73.751753
90                 Eltingville  0.065934               0  40.542231 -74.164331
258                 St. Albans  0.089888               0  40.694445 -73.758676
283                  Wakefield  0.070000               0  40.894705 -73.847201
161                      Malba  0.040000               0  40.790602 -73.826678
132                  Homecrest  0.040000               0  40.598525 -73.959185
18                  Beechhurst  0.042105               0  40.792781 -73.804365
133               Howard Beach  0.040000               0  40.654225 -73.838138
21                   Bellerose  0.040000               0  40.728573 -73.720128
9                   Bath Beach  0.040000               0  40.599519 -73.998752
13                  Baychester  0.040000               0  40.866858 -73.835798
294                Willowbrook  0.041667               0  40.603707 -74.132084
136                   Huguenot  0.051282               0  40.531912 -74.191741
292             Williamsbridge  0.060000               0  40.881039 

In [34]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Neighborhood'], ny_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [35]:
map_clusters.save('map_clusters.html')

In [36]:
ny_merged.loc[ny_merged['Cluster Labels'] == 0]

Neighborhood  Pharmacy  Cluster Labels   Latitude  Longitude
217       Prince's Bay  0.044444               0  40.526264 -74.201526
178        Mill Island  0.050000               0  40.606336 -73.908186
228     Remsen Village  0.040000               0  40.652117 -73.916653
54   Claremont Village  0.050000               0  40.831428 -73.901199
109         Georgetown  0.040000               0  40.623845 -73.916075
234           Rochdale  0.050000               0  40.675211 -73.772588
236      Rockaway Park  0.048387               0  40.580343 -73.841534
166      Manor Heights  0.046154               0  40.601810 -74.120594
244      Schuylerville  0.043011               0  40.826580 -73.826203
46   Castleton Corners  0.040000               0  40.613336 -74.119181
45         Castle Hill  0.038462               0  40.819014 -73.848027
87         Egbertville  0.040000               0  40.579119 -74.127272
42            Canarsie  0.060000               0  40.635564 -73.902093
41     Cambria Heights  0.083333               0  40.692775 -73.735269
40        Butler Manor  0.042553               0  40.506082 -74.229504
251          Soundview  0.040000               0  40.821012 -73.865746
59          Co-op City  0.050000               0  40.874294 -73.829939
115       Graniteville  0.040000               0  40.620172 -74.153152
182         Morrisania  0.040000               0  40.823592 -73.901506
98           Flatlands  0.040000               0  40.630446 -73.929113
91        Emerson Hill  0.050633               0  40.606794 -74.097762
201      Ocean Parkway  0.050000               0  40.613060 -73.968367
84            Edenwald  0.060000               0  40.884561 -73.848083
83         Eastchester  0.070000               0  40.887556 -73.827806
202           Old Town  0.040000               0  40.596329 -74.087511
203          Olinville  0.040000               0  40.871371 -73.863324
204         Ozone Park  0.040000               0  40.680708 -73.843203
205    Paerdegat Basin  0.060000               0  40.631318 -73.902335
77       East Flatbush  0.050000               0  40.641718 -73.936103
210     Pelham Gardens  0.040000               0  40.862966 -73.841612
212    Pleasant Plains  0.039474               0  40.524699 -74.219831
192    New Springville  0.050000               0  40.594252 -74.164960
71        Dongan Hills  0.040000               0  40.588673 -74.096399
138        Hunts Point  0.064103               0  40.809730 -73.883315
67        Country Club  0.040000               0  40.844246 -73.824099
221     Queens Village  0.040000               0  40.718893 -73.738715
36          Brookville  0.042553               0  40.660003 -73.751753
90         Eltingville  0.065934               0  40.542231 -74.164331
258         St. Albans  0.089888               0  40.694445 -73.758676
283          Wakefield  0.070000               0  40.894705 -73.847201
161              Malba  0.040000               0  40.790602 -73.826678
132          Homecrest  0.040000               0  40.598525 -73.959185
18          Beechhurst  0.042105               0  40.792781 -73.804365
133       Howard Beach  0.040000               0  40.654225 -73.838138
21           Bellerose  0.040000               0  40.728573 -73.720128
9           Bath Beach  0.040000               0  40.599519 -73.998752
13          Baychester  0.040000               0  40.866858 -73.835798
294        Willowbrook  0.041667               0  40.603707 -74.132084
136           Huguenot  0.051282               0  40.531912 -74.191741
292     Williamsbridge  0.060000               0  40.881039 -73.857446
121         Greenridge  0.044944               0  40.555295 -74.170794
261      Starrett City  0.060000               0  40.647589 -73.879370
1             Annadale  0.050000               0  40.538114 -74.178549
298           Woodlawn  0.070707               0  40.898273 -73.867315
118          Gravesend  0.050000               0  40.595260 -73.973471
297          Woodhaven  0.050000  

In [37]:
ny_merged.loc[ny_merged['Cluster Labels'] == 1]

Neighborhood  Pharmacy  Cluster Labels   Latitude  Longitude
194               North Corona  0.000000               1  40.754071 -73.857518
144                 Kensington  0.000000               1  40.642382 -73.980421
142            Jamaica Estates  0.010000               1  40.716805 -73.787227
193                       Noho  0.000000               1  40.723259 -73.988434
196                 North Side  0.000000               1  40.714823 -73.958809
145                Kew Gardens  0.000000               1  40.705179 -73.829819
143              Jamaica Hills  0.010000               1  40.711460 -73.796465
188               New Brighton  0.010000               1  40.640615 -74.087017
186                Murray Hill  0.000000               1  40.764126 -73.812763
147                Kingsbridge  0.010000               1  40.881687 -73.902818
186                Murray Hill  0.000000               1  40.748303 -73.978332
162            Manhattan Beach  0.010000               1  40.577914 -73.943537
159            Lower East Side  0.000000               1  40.717807 -73.980890
164           Manhattan Valley  0.000000               1  40.797307 -73.964286
157           Long Island City  0.000000               1  40.750217 -73.939202
167                Marble Hill  0.010000               1  40.876551 -73.910660
155               Little Italy  0.000000               1  40.719324 -73.997305
153             Lincoln Square  0.000000               1  40.773529 -73.985338
151                 Lenox Hill  0.000000               1  40.768113 -73.958860
172             Middle Village  0.010000               1  40.716415 -73.881143
174                    Midtown  0.000000               1  40.754691 -73.981669
300                   Woodside  0.010000               1  40.746349 -73.901842
175              Midtown South  0.000000               1  40.748510 -73.988713
148        Kingsbridge Heights  0.000000               1  40.870392 -73.901523
179        Morningside Heights  0.010000               1  40.808000 -73.963896
180             Morris Heights  0.000000               1  40.847898 -73.919672
181                Morris Park  0.010000               1  40.847549 -73.850402
184                 Mount Eden  0.000000               1  40.843826 -73.916556
146          Kew Gardens Hills  0.000000               1  40.722578 -73.820878
165             Manhattanville  0.010000               1  40.816934 -73.957385
150                Lefrak City  0.000000               1  40.736075 -73.862525
198            Oakland Gardens  0.010000               1  40.745619 -73.754950
262                   Steinway  0.000000               1  40.775923 -73.902290
263            Stuyvesant Town  0.000000               1  40.731000 -73.974052
266                Sunset Park  0.000000               1  40.645103 -74.010316
267               Sutton Place  0.000000               1  40.760280 -73.963556
273                    Tribeca  0.000000               1  40.721522 -74.010683
274                 Tudor City  0.000000               1  40.746917 -73.971219
275                 Turtle Bay  0.000000               1  40.752042 -73.967708
277         University Heights  0.010000               1  40.855727 -73.910416
278            Upper East Side  0.000000               1  40.775639 -73.960508
279            Upper West Side  0.000000               1  40.787658 -73.977059
281                   Van Nest  0.010000               1  40.843608 -73.866299
282               Vinegar Hill  0.000000               1  40.703321 -73.981116
284         Washington Heights  0.000000               1  40.851903 -73.936900
285                 Weeksville  0.000000               1  40.675040 -73.930531
286              West Brighton  0.000000               1  40.631879 -74.107182
287                 West Farms  0.000000               1  40.839475 -73.877745
288               West Village  0.000000               1  40.734434 -74.006180
289         Westchester Square  0.010000               1  40.840619 

In [38]:
ny_merged.loc[ny_merged['Cluster Labels'] == 2]

Neighborhood  Pharmacy  Cluster Labels   Latitude  Longitude
256  Springfield Gardens  0.034884               2  40.666230 -73.760421
272               Travis  0.033333               2  40.586314 -74.190737
4               Arrochar  0.025641               2  40.596313 -74.067124
3              Arlington  0.018868               2  40.635325 -74.165104
253        South Jamaica  0.030000               2  40.696911 -73.790426
26            Bloomfield  0.031250               2  40.605779 -74.187256
38            Bulls Head  0.030000               2  40.609592 -74.159409
2          Arden Heights  0.021505               2  40.549286 -74.185887
299              Woodrow  0.032787               2  40.541968 -74.205246
24          Bergen Beach  0.032609               2  40.615150 -73.898556
247          Shore Acres  0.025316               2  40.609719 -74.066678
246       Sheepshead Bay  0.030000               2  40.586890 -73.943186
252          South Beach  0.022989               2  40.580247 -74.079553
270        Tompkinsville  0.020000               2  40.637316 -74.080554
264            Sunnyside  0.020690               2  40.612760 -74.097126
23           Bensonhurst  0.020000               2  40.611009 -73.995180
15             Bayswater  0.025000               2  40.611322 -73.765968
264            Sunnyside  0.020690               2  40.740176 -73.926916
265    Sunnyside Gardens  0.020000               2  40.745652 -73.918193
12           Bay Terrace  0.021739               2  40.553988 -74.139166
32         Broad Channel  0.023810               2  40.603027 -73.820055
12           Bay Terrace  0.021739               2  40.782843 -73.776802
19              Bellaire  0.020000               2  40.733014 -73.738892
245             Sea Gate  0.022222               2  40.576375 -74.007873
280               Utopia  0.020000               2  40.733500 -73.796717
20          Belle Harbor  0.018519               2  40.576156 -73.854018
290          Westerleigh  0.030000               2  40.621090 -74.133041
260            Stapleton  0.020000               2  40.626928 -74.077902
291           Whitestone  0.030000               2  40.781291 -73.814202
268          Throgs Neck  0.035088               2  40.815109 -73.816350
8             Auburndale  0.030000               2  40.761730 -73.791762
259           St. George  0.021053               2  40.644982 -74.079353
276            Unionport  0.030000               2  40.829774 -73.850535
257       Spuyten Duyvil  0.020000               2  40.881395 -73.917190
141       Jamaica Center  0.020000               2  40.704657 -73.796902
242                Rugby  0.020000               2  40.655572 -73.926882
185           Mount Hope  0.020202               2  40.848842 -73.908299
183           Mott Haven  0.025000               2  40.806239 -73.916100
177           Mill Basin  0.030000               2  40.615974 -73.915154
176              Midwood  0.020000               2  40.625596 -73.957595
106            Fox Hills  0.021978               2  40.617311 -74.081740
107        Fresh Meadows  0.020000               2  40.734394 -73.782713
173        Midland Beach  0.020000               2  40.573527 -74.093483
171              Melrose  0.020000               2  40.819754 -73.909422
170              Maspeth  0.021277               2  40.725427 -73.896217
169     Mariner's Harbor  0.020619               2  40.632546 -74.150085
168          Marine Park  0.030000               2  40.609748 -73.931344
110      Gerritsen Beach  0.020000               2  40.590848 -73.930102
112             Glendale  0.020000               2  40.702762 -73.870742
163    Manhattan Terrace  0.020000               2  40.614433 -73.957438
116           Grant City  0.030000               2  40.576216 -74.105856
160              Madison  0.020000               2  40.609378 -73.948415
117             Grasmere  0.030000               2  40.598268 -74.076674
156          Little Neck  0.021277               2  40.770826 -73.7388